In [1]:
import sys
sys.executable

'd:\\code\\its\\venv-its\\Scripts\\python.exe'

In [2]:
import utils
import importlib
importlib.reload(utils)

ModuleNotFoundError: No module named 'utils'

In [1]:
import os
import pandas as pd
import plotly.express as px
# from utils import config, connect_to_db

pd.set_option('display.max_rows', 100)

In [2]:
import traffic_map
import importlib
importlib.reload(traffic_map)

from traffic_map import read_data_vehicle, preprocessing, insert_heading_col, find_closest_point, get_map_color

# read data

In [5]:
DATE = '2024-07-03'

In [6]:
schema = config.get('TableGPS', 'schema')
tbl_name = config.get('TableGPS', 'tbl_name')

sql = f'''
    SELECT * FROM {schema}.{tbl_name}
    where date(datetime) = '{DATE}'
'''

conn = connect_to_db()
df = pd.read_sql(sql, conn)
conn.close()

In [12]:
df.rename(columns={'x':'y', 'y':'x'}, inplace=True)
df['vehicle'] = df['vehicle'].str.replace('-','').str.replace('.','')
df['hour'] = df['datetime'].dt.hour
df['min'] = df['datetime'].dt.minute
df['sec'] = df['datetime'].dt.second
df['time'] = df['datetime'].astype(str).str[-8:]

In [13]:
df['vehicle'].str[:2].value_counts()

vehicle
29    7549776
22      79680
30      18889
34      13800
50      10988
36       6922
98       6700
51       4695
88       3035
37       1290
14        979
26        588
Name: count, dtype: int64

In [23]:
df

vehicle            datetime           x          y  speed  \
0        29H-918.69 2024-07-03 00:00:00  105.957053  20.991053    0.0   
1        29F-019.43 2024-07-03 00:00:00  105.750819  21.007403    0.0   
2        29F-019.29 2024-07-03 00:00:09  105.750824  21.007472    0.0   
3        29F-008.76 2024-07-03 00:00:09  105.750749  21.007158    0.0   
4        29F-008.67 2024-07-03 00:00:09  105.957656  20.991028    0.0   
...             ...                 ...         ...        ...    ...   
7697337  29F-020.93 2024-07-03 23:33:45  105.957167  20.991004    0.0   
7697338  29F-020.93 2024-07-03 23:33:25  105.957191  20.991017    0.0   
7697339  29F-020.93 2024-07-03 23:33:05  105.957181  20.990974    0.0   
7697340  29F-020.93 2024-07-03 23:32:45  105.957199  20.990929    0.0   
7697341  29F-020.93 2024-07-03 23:32:25  105.957197  20.990957    0.0   

               arrival_time  hour  min  sec      time  
0       2024-07-03 00:00:01     0    0    0  00:00:00  
1       2024-07-03 00:00:01     0    0    0  00:00:00  
2       2024-07-03 00:00:10     0    0    9  00:00:09  
3       2024-07-03 00:00:10     0    0    9  00:00:09  
4       2024-07-03 00:00:10     0    0    9  00:00:09  
...                     ...   ...  ...  ...       ...  
7697337 2024-07-05 05:59:43    23   33   45  23:33:45  
7697338 2024-07-05 05:59:43    23   33   25  23:33:25  
7697339 2024-07-05 05:59:43    23   33    5  23:33:05  
7697340 2024-07-05 05:59:43    23   32   45  23:32:45  
7697341 2024-07-05 05:59:43    23   32   25  23:32:25  

[7697342 rows x 10 columns]

In [42]:
df_16 = df[(df['time']>='15:45:00') & (df['time']<='16:05:00')]
df_16 = df_16.sort_values(by=['vehicle', 'datetime']).reset_index(drop=True)
df_16.shape

(129111, 10)

In [ ]:
# df_16.to_csv('f_gps_vehicle.csv', index=False)

# var

In [3]:
# DATE = datetime.now().strftime('%Y-%m-%d')
# TIME = datetime.now().strftime('%H:%M:00')

DATE = '2024-07-03'
TIME = '16:00:00'

print(f'DATE = {DATE}')
print(f'TIME = {TIME}')

current_path = os.path.dirname(os.path.abspath(__name__))
file_path = f'{current_path}/../db/traffic.xlsx'
FILE_PATH_VEHICLE = f'{current_path}/../db/f_gps_vehicle.csv'
FILE_PATH_STREET = f'{current_path}/../db/d_street.csv'

DATE = 2024-07-03
TIME = 16:00:00


# vehicle

In [4]:
df_vehicle = read_data_vehicle(FILE_PATH_VEHICLE, DATE, TIME, duration=5)
df_vehicle = preprocessing(df_vehicle)
print(df_vehicle.shape)

(129111, 10)
(32039, 10)
(25126, 10)
(13926, 10)
(10524, 19)


In [5]:
df_vehicle['vehicle'].nunique()

970

In [112]:
df_vehicle.describe()

datetime             y             x  \
count                          10524  10524.000000  10524.000000   
mean   2024-07-03 15:57:29.683010304    105.820427     21.015088   
min              2024-07-03 15:55:01    105.730057     20.940079   
25%              2024-07-03 15:56:15    105.787216     20.993004   
50%              2024-07-03 15:57:30    105.820880     21.017348   
75%              2024-07-03 15:58:43    105.847571     21.036907   
max              2024-07-03 16:00:00    105.929901     21.089949   
std                              NaN      0.042765      0.034010   

              speed   speed_last  duration_last   speed_next  duration_next  \
count  10524.000000  9775.000000    9775.000000  9805.000000    9805.000000   
mean      18.007222    17.598486      22.924501    17.539031      23.095563   
min        0.000000     0.000000       5.000000     0.000000       5.000000   
25%        7.000000     5.800000      10.000000     5.000000      10.000000   
50%       18.000000    17.000000      30.000000    17.000000      30.000000   
75%       27.000000    27.000000      30.000000    27.000000      30.000000   
max       78.000000    78.000000     180.000000    76.000000     180.000000   
std       13.344357    13.419024      10.554575    13.490076      11.161830   

       distance_last  distance_next  speed_avg_last  speed_avg_next  \
count    9775.000000    9805.000000     9775.000000     9805.000000   
mean      117.320336     114.490899       18.951822       18.673853   
min         0.000000       0.000000        0.000000        0.000000   
25%        45.893351      44.736517        9.512046        9.245753   
50%        95.094447      94.014746       18.056301       17.922346   
75%       167.044261     166.037499       26.333572       26.237121   
max      3192.761553    2252.699802      200.083064      136.797176   
std       112.096026      95.516481       13.049525       12.458245   

       is_accelerate   accelerate     speed_avg      heading  
count   10524.000000  9063.000000  10524.000000  9805.000000  
mean       -0.130844    -0.006807     17.745557   176.271336  
min        -1.000000    -4.373783      0.096092     0.000000  
25%        -1.000000    -0.322176      9.753924    84.489039  
50%        -1.000000     0.001193     16.011096   177.755417  
75%         1.000000     0.327914     23.708349   277.378864  
max         1.000000     3.957072     78.000000   359.987808  
std         0.988330     0.631924     11.235745   108.145852

In [72]:
20*1000/3600*30

166.66666666666666

In [114]:
df_plot = df_vehicle

color_scale = [(0, 'orange'), (1,'red')]

fig = px.scatter_mapbox(df_plot, 
                        lat="x", 
                        lon="y", 
                        # hover_name="distance", 
                        hover_data=['vehicle', 'datetime', 'speed'],
                        # color="Listed",
                        # color_continuous_scale=color_scale,
                        # size='dummy_column_for_size',
                        zoom=8, 
                        height=800,
                        width=800).update_traces(marker={"size": 10})

fig.update_layout(mapbox_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

# street

In [81]:
df_street = pd.read_csv(FILE_PATH_STREET)
df_street_type = pd.read_excel(file_path, sheet_name='street')
df_street = df_street.merge(df_street_type, how='left', on='street')
df_street.shape

(15091, 6)

In [75]:
df_street.head()

street          x           y  direction  order         type  \
0  An Dương Vương bé  21.081620  105.818046         -1      1  đường chính   
1  An Dương Vương bé  21.081699  105.818004         -1      2  đường chính   
2  An Dương Vương bé  21.081778  105.817957         -1      3  đường chính   
3  An Dương Vương bé  21.081855  105.817909         -1      4  đường chính   
4  An Dương Vương bé  21.081932  105.817859         -1      5  đường chính   

      heading  
0  333.090084  
1  331.109932  
2  329.411334  
3  329.179143  
4  329.127840

In [20]:
df_plot = df_street

color_scale = [(0, 'orange'), (1,'red')]

fig = px.scatter_mapbox(df_plot, 
                        lat="x", 
                        lon="y", 
                        # hover_name="distance", 
                        hover_data=['street', 'direction', 'order', 'heading'],
                        # color="Listed",
                        # color_continuous_scale=color_scale,
                        # size='dummy_column_for_size',
                        zoom=8, 
                        height=800,
                        width=800).update_traces(marker={"size": 10})

fig.update_layout(mapbox_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

# map

sửa order null, order = x, Hàng Dậu -> Hàng Đậu

In [168]:
df_street.head()

street          x           y  direction  order     heading
0  An Dương Vương bé  21.081620  105.818046         -1      1  333.090084
1  An Dương Vương bé  21.081699  105.818004         -1      2  331.109932
2  An Dương Vương bé  21.081778  105.817957         -1      3  329.411334
3  An Dương Vương bé  21.081855  105.817909         -1      4  329.179143
4  An Dương Vương bé  21.081932  105.817859         -1      5  329.127840

In [82]:
df_street = df_street[df_street['order'].notnull() & (df_street['order'] != 'x')].reset_index(drop=True)
df_street['order'] = df_street['order'].astype(int)
df_street.shape

(14978, 6)

In [83]:
df_street[['street', 'direction', 'order']].drop_duplicates().shape

(14978, 3)

In [84]:
df_street = insert_heading_col(df_street)
df_vehicle = find_closest_point(df_vehicle, df_street, angle_threshold=45)

distance_closest_threshold = 10
df_vehicle = df_vehicle[df_vehicle['distance_closest']<=distance_closest_threshold]
df_vehicle.shape

d:\code\its\traffic_map\traffic_map.py:144: FutureWarning: A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.


  df['heading'] + 360
d:\code\its\traffic_map\traffic_map.py:144: FutureWarning: Series.fillna with 'method' is deprecated and will raise in a future version. Use obj.ffill() or obj.bfill() instead.
  df['heading'] + 360


MemoryError: Unable to allocate 571. MiB for an array with shape (5000, 14978) and data type float64

In [40]:
import traffic_map
import importlib
importlib.reload(traffic_map)

from traffic_map import read_data_vehicle, preprocessing, insert_heading_col, find_closest_point, get_map_color

In [49]:
df_color_mapping = pd.read_excel(file_path, sheet_name='color')

In [50]:
df_color_mapping

type    color  speed_in_traffic_min  speed_in_traffic_max
0       cao tốc    green                    40                  1000
1       cao tốc   yellow                    25                    40
2       cao tốc      red                    15                    25
3       cao tốc  darkred                    -1                    15
4      vành đai    green                    25                  1000
5      vành đai   yellow                    15                    25
6      vành đai      red                    10                    15
7      vành đai  darkred                    -1                    10
8   đường chính    green                    25                  1000
9   đường chính   yellow                    15                    25
10  đường chính      red                    10                    15
11  đường chính  darkred                    -1                    10
12  đường nhánh    green                    15                  1000
13  đường nhánh   yellow                    10                    15
14  đường nhánh      red                     5                    10
15  đường nhánh  darkred                    -1                     5

In [76]:
df_street_color, df_rolling = get_map_color(df_vehicle, df_street, window_size=10)

KeyError: "['x_closest', 'y_closest'] not in index"

In [8]:
df_rolling.shape

NameError: name 'df_rolling' is not defined

In [53]:
df_rolling = df_rolling.merge(df_color_mapping, how='left', on='type')

In [55]:
df_rolling.shape

(57536, 10)

In [60]:
df_rolling[
    (
        (df_rolling['speed_median']>=df_rolling['speed_in_traffic_min']) & 
        (df_rolling['speed_median']<df_rolling['speed_in_traffic_max'])
    ) | (
        df_rolling['speed_median'].isnull()
    )
].shape

(39926, 10)

In [ ]:
df_rolling

In [54]:
df_rolling.head()

street         type  direction  \
0  An Dương Vương bé  đường chính         -1   
1  An Dương Vương bé  đường chính         -1   
2  An Dương Vương bé  đường chính         -1   
3  An Dương Vương bé  đường chính         -1   
4  An Dương Vương bé  đường chính         -1   

                              order                                 speed_avg  \
0   [1, 2, 3, 4, 5, 6, 7, 8, 9, 10]  [22.782983820195533, 28.300170058885918]   
1   [1, 2, 3, 4, 5, 6, 7, 8, 9, 10]  [22.782983820195533, 28.300170058885918]   
2   [1, 2, 3, 4, 5, 6, 7, 8, 9, 10]  [22.782983820195533, 28.300170058885918]   
3   [1, 2, 3, 4, 5, 6, 7, 8, 9, 10]  [22.782983820195533, 28.300170058885918]   
4  [2, 3, 4, 5, 6, 7, 8, 9, 10, 11]                      [28.300170058885918]   

   speed_median color_x  color_y  speed_in_traffic_min  speed_in_traffic_max  
0     25.541577   green    green                    25                  1000  
1     25.541577   green   yellow                    15                    25  
2     25.541577   green      red                    10                    15  
3     25.541577   green  darkred                    -1                    10  
4     28.300170   green    green                    25                  1000

In [132]:
df_street_color.head(10)

street          x           y  direction  order     heading  \
0  An Dương Vương bé  21.081620  105.818046         -1      1  333.090084   
1  An Dương Vương bé  21.081699  105.818004         -1      2  331.109932   
2  An Dương Vương bé  21.081778  105.817957         -1      3  329.411334   
3  An Dương Vương bé  21.081855  105.817909         -1      4  329.179143   
4  An Dương Vương bé  21.081932  105.817859         -1      5  329.127840   
5  An Dương Vương bé  21.082009  105.817810         -1      6  329.179170   
6  An Dương Vương bé  21.082087  105.817761         -1      7  335.121167   
7  An Dương Vương bé  21.082167  105.817721         -1      8  331.159307   
8  An Dương Vương bé  21.082246  105.817675         -1      9  329.743227   
9  An Dương Vương bé  21.082324  105.817627         -1     10  329.743240   

              speed_avg  color  
0  [22.782983820195533]  green  
1                 [nan]  green  
2                 [nan]  green  
3                 [nan]  green  
4                 [nan]  green  
5                 [nan]  green  
6  [28.300170058885918]  green  
7                 [nan]  green  
8                 [nan]  green  
9                 [nan]  green

In [86]:
df_street_color[['street', 'x', 'y', 'direction', 'order', 'color']]

street          x           y  direction  order  color
0      An Dương Vương bé  21.081620  105.818046         -1      1  green
1      An Dương Vương bé  21.081699  105.818004         -1      2  green
2      An Dương Vương bé  21.081778  105.817957         -1      3  green
3      An Dương Vương bé  21.081855  105.817909         -1      4  green
4      An Dương Vương bé  21.081932  105.817859         -1      5  green
...                  ...        ...         ...        ...    ...    ...
14973      Đội Cấn nhánh  21.037733  105.807001          1      5    NaN
14974      Đội Cấn nhánh  21.037735  105.806905          1      6    NaN
14975      Đội Cấn nhánh  21.037737  105.806809          1      7    NaN
14976      Đội Cấn nhánh  21.037739  105.806713          1      8    NaN
14977      Đội Cấn nhánh  21.037738  105.806677          1      9    NaN

[14978 rows x 6 columns]

In [85]:
df_street_color.columns

Index(['street', 'x', 'y', 'direction', 'order', 'type', 'heading',
       'speed_avg', 'color'],
      dtype='object')

In [133]:
df_plot = df_street_color.copy()
df_plot['speed_avg'] = df_plot['speed_avg'].astype(str)

# 21.020570	105.801486

# Custom color mapping with RGB values
color_discrete_map = {
    'green': 'rgb(22, 224, 152)',
    'yellow': 'rgb(255, 207, 67)',
    'red': 'rgb(242, 78, 66)',
    'darkred': 'rgb(169, 39, 39)',
    'blue': 'blue'
}

fig = px.scatter_mapbox(df_plot, 
                        lat="x", 
                        lon="y", 
                        # hover_name="distance", 
                        hover_data=['street', 'x', 'y', 'direction', 'order', 'heading', 'speed_avg', 'color'],
                        color="color",
                        color_discrete_map=color_discrete_map,
                        # color_continuous_scale=color_scale,
                        # size='dummy_column_for_size',
                        zoom=8, 
                        height=800,
                        width=800).update_traces(marker={"size": 10})

fig.update_layout(mapbox_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

# plot check

In [211]:
df_vehicle = df_test[['x', 'y', 'time']]
df_vehicle['type'] = 'vehicle'
df_route = df_test[['x_closest', 'y_closest', 'time']].rename(columns={'x_closest': 'x', 'y_closest': 'y'})
df_route['type'] = 'route'

df_plot = pd.concat([df_vehicle, df_route])

fig = px.scatter_mapbox(df_plot, 
                        lat="x", 
                        lon="y", 
                        # hover_name="distance", 
                        hover_data=['x', 'y', 'time'],
                        color="type",
                        # color_continuous_scale=color_scale,
                        # size='dummy_column_for_size',
                        zoom=8, 
                        height=800,
                        width=800).update_traces(marker={"size": 10})

fig.update_layout(mapbox_style="open-street-map")
fig.update_layout(margin={"r":0,"t":0,"l":0,"b":0})
fig.show()

C:\Users\h\AppData\Local\Temp\ipykernel_3260\3303662944.py:2: SettingWithCopyWarning:


A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy

